In [ ]:
! pip install eli5
import eli5

In [ ]:
from sklearn.datasets import fetch_20newsgroups
from sklearn.feature_extraction.text import CountVectorizer, TfidfVectorizer
from sklearn.linear_model import LogisticRegression
from sklearn.ensemble import GradientBoostingClassifier
from sklearn.pipeline import Pipeline
from sklearn.model_selection import GridSearchCV, StratifiedKFold
from sklearn.metrics import accuracy_score, classification_report
import pandas as pd
import re

In [ ]:
import certifi
import ssl
import urllib.request
from sklearn.datasets import fetch_20newsgroups

# Set the SSL certificate bundle path to the latest version
ssl_context = ssl.create_default_context(cafile=certifi.where())
urllib.request.install_opener(urllib.request.build_opener(urllib.request.HTTPSHandler(context=ssl_context)))

In [ ]:
train = fetch_20newsgroups()
test = fetch_20newsgroups(subset="test")

In [ ]:
train.data[95]

"From: coburnn@spot.Colorado.EDU (Nicholas S. Coburn)\nSubject: Re: bikes with big dogs\nNntp-Posting-Host: spot.colorado.edu\nOrganization: University of Colorado, Boulder\nLines: 19\n\nIn article <1993Apr14.234835.1@cua.edu> 84wendel@cua.edu writes:\n>Has anyone ever heard of a rider giving a big dog such as a great dane a ride \n>on the back of his bike.  My dog would love it if I could ever make it work.\n>\tThanks\n>\t\t\t84wendel@cua.edu\n>\n\nOn the back might be tricky, but here in Boulder, there is a guy \nthat can always be seen with his Golden Retriever in the sidecar.\nOf course, the dog is always wearing WWII style goggles (no joke)\n\n\n________________________________________________________________________\nNick Coburn                     DoD#6425                      AMA#679817\n                  '88CBR1000              '89CBR600\n                       coburnn@spot.colorado.edu\n________________________________________________________________________\n\n\n"

In [ ]:
len(train.data)

11314

# pre-processing

In [ ]:
import numpy as np
from sklearn.utils import Bunch

In [ ]:
train_1 = fetch_20newsgroups(remove=('headers', 'footers', 'quotes'))
test_1 = fetch_20newsgroups(subset="test", remove=('headers', 'footers', 'quotes'))

In [ ]:
train_2 = fetch_20newsgroups(remove=( 'footers', 'quotes'))
test_2 = fetch_20newsgroups(subset="test", remove=('footers', 'quotes'))

In [ ]:
train_3 = fetch_20newsgroups(remove=( 'footers'))
test_3 = fetch_20newsgroups(subset="test", remove=('footers'))

In [ ]:
def clean_text(news_data):
    """Cleans some issues with the text data
    Args:
        news_data: list of text strings
    Returns:
        A cleaned version of the input data
    """
    cleaned_text = []
    for text in news_data.data:
        x = re.sub('[^\w]|_', ' ', text)  # only keep numbers and letters and spaces
        x = x.lower()
        x = re.sub(r'[^\x00-\x7f]',r'', x)  # remove non ascii texts
        x = ' '.join([y for y in x.split(' ') if y]) # remove empty words
        x = re.sub(r'\b\d+\b', '[number]', x) # convert all numbers to '[number]' to reduce vocab size.
        cleaned_text.append(x)

    return Bunch(
        data=np.array(cleaned_text),
        target=news_data.target,
        target_names=news_data.target_names,
        DESCR=news_data.DESCR,
        filenames=news_data.filenames,
    )

In [ ]:
cleaned_train = clean_text(train)
cleaned_test =  clean_text(test)

In [ ]:
cleaned_train_1 = clean_text(train_1)
cleaned_test_1 =  clean_text(test_1)

In [ ]:
cleaned_train_2 = clean_text(train_2)
cleaned_test_2 =  clean_text(test_2)

In [ ]:
cleaned_train_3 = clean_text(train_3)
cleaned_test_3 =  clean_text(test_3)

In [ ]:
train_1.data[95]

'\nOn the back might be tricky, but here in Boulder, there is a guy \nthat can always be seen with his Golden Retriever in the sidecar.\nOf course, the dog is always wearing WWII style goggles (no joke)\n'

In [ ]:
train_2.data[95]

'From: coburnn@spot.Colorado.EDU (Nicholas S. Coburn)\nSubject: Re: bikes with big dogs\nNntp-Posting-Host: spot.colorado.edu\nOrganization: University of Colorado, Boulder\nLines: 19\n\n\nOn the back might be tricky, but here in Boulder, there is a guy \nthat can always be seen with his Golden Retriever in the sidecar.\nOf course, the dog is always wearing WWII style goggles (no joke)\n'

In [ ]:
cleaned_train.data[95]

In [ ]:
cleaned_train_1.data[95]

'on the back might be tricky but here in boulder there is a guy that can always be seen with his golden retriever in the sidecar of course the dog is always wearing wwii style goggles no joke'

In [ ]:
cleaned_train_2.data[95]

'from coburnn spot colorado edu nicholas s coburn subject re bikes with big dogs nntp posting host spot colorado edu organization university of colorado boulder lines [number] on the back might be tricky but here in boulder there is a guy that can always be seen with his golden retriever in the sidecar of course the dog is always wearing wwii style goggles no joke'

перевіряю на бейзлайні вплив різних типів препроцесингу даних

In [ ]:
pipeline = Pipeline([
    ('bow', CountVectorizer()),
    ('clf', LogisticRegression(C=1)),
])

In [ ]:
pipeline.fit(train["data"], train["target"])
pipeline.fit(train_1["data"], train_1["target"])
pipeline.fit(train_2["data"], train_2["target"])
pipeline.fit(train_3["data"], train_3["target"])
pipeline.fit(cleaned_train["data"], cleaned_train["target"])
pipeline.fit(cleaned_train_1["data"], cleaned_train_1["target"])
pipeline.fit(cleaned_train_2["data"], cleaned_train_2["target"])

In [ ]:
predictions = pipeline.predict(test["data"])
predictions_1 = pipeline.predict(test_1["data"])
predictions_2 = pipeline.predict(test_2["data"])
predictions_3 = pipeline.predict(cleaned_test["data"])
predictions_4 = pipeline.predict(cleaned_test_1["data"])
predictions_5 = pipeline.predict(cleaned_test_2["data"])
predictions_6 = pipeline.predict(test_3["data"])


In [ ]:
scores = [
    accuracy_score(test["target"], predictions),
    accuracy_score(test_1["target"], predictions_1),
    accuracy_score(test_2["target"], predictions_2),
    accuracy_score(test_3["target"], predictions_6),
    accuracy_score(cleaned_test["target"], predictions_3),
    accuracy_score(cleaned_test_1["target"], predictions_4),
    accuracy_score(cleaned_test_2["target"], predictions_5)

]

In [ ]:
df = pd.DataFrame({"Test Set": ["Test", "Test 1 (without h,f,q)", "Test 2 (without f,q)", "Test 3 (without f)", "Cleaned Test", "Cleaned Test 1 (without h,f,q)", "Cleaned Test 2 (without f,q"], "Accuracy Score": scores})

In [ ]:
df

Test Set  Accuracy Score
0                            Test        0.729687
1          Test 1 (without h,f,q)        0.545273
2            Test 2 (without f,q)        0.674588
3              Test 3 (without f)        0.719331
4                    Cleaned Test        0.735661
5  Cleaned Test 1 (without h,f,q)        0.546999
6     Cleaned Test 2 (without f,q        0.679501

Висновки:
- наявність елементів ‘headers’ ‘footers’ ‘quotes’ сприяє кращому результату класифікації (за результатами експерименту, є сенс перевірити дані без футерів)
- застосування "технічних" (def clean_text) поправок до даних дали мінімальні покращення на рівні сотих

# experiments with different models and hyperparameters

In [ ]:
skf = StratifiedKFold(n_splits=3, shuffle=True, random_state=1)

In [ ]:
pipeline = Pipeline([
    ('vect', CountVectorizer()),
    ('clf', LogisticRegression())
])

params = {
    'vect__ngram_range': [(1, 1), (1, 2)],
    'vect__max_features': [5000, 10000],
    'vect__min_df': [1, 2, 5],
    'vect__max_df': [1.0, 0.8, 0.5],
    'clf__C': [10, 1, 0.1, 0.01]
}
grid_search = GridSearchCV(pipeline, params, scoring="accuracy", cv=skf, n_jobs=-1)

In [ ]:
grid_search.fit(train["data"], train["target"])

In [ ]:
grid_search.best_score_, grid_search.best_estimator_

(0.8542509068340657,
 Pipeline(steps=[('vect',
                  CountVectorizer(max_df=0.5, max_features=10000, min_df=5)),
                 ('clf', LogisticRegression(C=0.1))]))

In [ ]:
pipeline = Pipeline([
    ('vect', CountVectorizer(max_df=0.5, max_features=10000, min_df=5)),
    ('clf', LogisticRegression(C=0.1)),
])
pipeline.fit(train["data"], train["target"])

/Users/oleksandra/machine_learning_projector/venv/lib/python3.11/site-packages/sklearn/linear_model/_logistic.py:458: ConvergenceWarning: lbfgs failed to converge (status=1):
STOP: TOTAL NO. of ITERATIONS REACHED LIMIT.

Increase the number of iterations (max_iter) or scale the data as shown in:
    https://scikit-learn.org/stable/modules/preprocessing.html
Please also refer to the documentation for alternative solver options:
    https://scikit-learn.org/stable/modules/linear_model.html#logistic-regression
  n_iter_i = _check_optimize_result(


Pipeline(steps=[('vect',
                 CountVectorizer(max_df=0.5, max_features=10000, min_df=5)),
                ('clf', LogisticRegression(C=0.1))])

In [ ]:
predictions = pipeline.predict(test["data"])
accuracy_score(test["target"], predictions)

0.780801911842804

In [ ]:
predictions = pipeline.predict(cleaned_test["data"])
accuracy_score(cleaned_test["target"], predictions)

0.7092405735528412

In [ ]:
predictions = pipeline.predict(test_3["data"])
accuracy_score(test_3["target"], predictions)

0.7618162506638343

In [ ]:
report = classification_report(test["target"], predictions, output_dict=True)

In [ ]:
results = {
        'Vectorizer': 'vect',
        'Hyperparameters': grid_search.best_params_,
        'Algorithm': 'clf',
        'Cross-validation score': grid_search.best_score_,
        'Test score': accuracy_score,
        'Classification report': report

    }

In [ ]:
pipeline_1 = Pipeline([
    ('vect', TfidfVectorizer()),
    ('clf', LogisticRegression())
])

params_1 = {
    'vect__ngram_range': [(1, 1), (1, 2), (1, 3)],
    'vect__max_features': [1000, 5000, 10000],
    'vect__min_df': [1, 2, 5],
    'vect__max_df': [1, 0.8, 0.5],
    'clf__C': [10, 1, 0.1, 0.01]
}


grid_search_1 = GridSearchCV(pipeline_1, params_1, scoring="accuracy", cv=skf, n_jobs=-1)

In [ ]:
grid_search_1.fit(train["data"], train["target"])
grid_search_1.best_score_, grid_search_1.best_estimator_

In [ ]:
grid_search_1.best_score_, grid_search_1.best_estimator_

(0.8908427405328324,
 Pipeline(steps=[('vect', TfidfVectorizer(max_df=0.5, max_features=10000)),
                 ('clf', LogisticRegression(C=10))]))

In [ ]:
pipeline_1 = Pipeline([
    ('vect', TfidfVectorizer(max_df=0.5, max_features=10000)),
    ('clf', LogisticRegression(C=10, max_iter = 1000)),
])
pipeline_1.fit(train["data"], train["target"])

Pipeline(steps=[('vect', TfidfVectorizer(max_df=0.5, max_features=10000)),
                ('clf', LogisticRegression(C=10, max_iter=1000))])

In [ ]:
predictions_1 = pipeline_1.predict(test["data"])
accuracy_score_1 = accuracy_score(test["target"], predictions_1)
accuracy_score(test["target"], predictions_1)

0.8210302708443973

In [ ]:
eli5.show_prediction(pipeline_1[1], test["data"][1500],  vec=pipeline_1[0],
feature_names=pipeline_1[0].get_feature_names_out(), target_names=test.target_names)

In [ ]:
report_1 = classification_report(test["target"], predictions_1, output_dict=True)

In [ ]:
results_1 = {
        'Vectorizer': 'TfidfVectorizer',
        'Hyperparameters': grid_search_1.best_params_,
        'Algorithm': 'LogisticRegression',
        'Cross-validation score': grid_search_1.best_score_,
        'Test score': accuracy_score_1,
        'Classification report': report_1

    }

In [ ]:
pipeline_2 = Pipeline([
    ('vect', TfidfVectorizer()),
    ('clf', GradientBoostingClassifier())
])

params_2 = {
    'vect__ngram_range': [(1, 1), (1, 2), (1, 3)],
    'vect__max_features': [1000, 5000, 10000],
    'vect__min_df': [1, 2, 5],
    'vect__max_df': [1, 0.8, 0.5],
    'clf__learning_rate': [0.01, 0.1, 0.5],
    'clf__n_estimators': [50, 100]

}


grid_search_2 = GridSearchCV(pipeline_2, params_2, scoring="accuracy", cv=skf, n_jobs=-1)

In [ ]:
grid_search_2.fit(train["data"], train["target"])

In [ ]:
grid_search_2.best_score_, grid_search_2.best_estimator_

(0.8064354402666852,
 Pipeline(steps=[('vect',
                  TfidfVectorizer(max_df=0.8, max_features=10000, min_df=2)),
                 ('clf', GradientBoostingClassifier())]))

In [ ]:
pipeline_2 = Pipeline([
    ('vect', TfidfVectorizer(max_df=0.8, max_features=10000, min_df=2)),
    ('clf', GradientBoostingClassifier()),
])
pipeline_2.fit(train["data"], train["target"])

Pipeline(steps=[('vect',
                 TfidfVectorizer(max_df=0.8, max_features=10000, min_df=2)),
                ('clf', GradientBoostingClassifier())])

In [ ]:
predictions_2 = pipeline_2.predict(test["data"])
accuracy_score_2 = accuracy_score(test["target"], predictions_2)
print(accuracy_score_2)

0.747344662772172


In [ ]:
report_2 = classification_report(test["target"], predictions_2, output_dict=True)

In [ ]:
report_2

{'0': {'precision': 0.7786259541984732,
  'recall': 0.6394984326018809,
  'f1-score': 0.7022375215146299,
  'support': 319},
 '1': {'precision': 0.6997455470737913,
  'recall': 0.7069408740359897,
  'f1-score': 0.7033248081841432,
  'support': 389},
 '2': {'precision': 0.6965174129353234,
  'recall': 0.7106598984771574,
  'f1-score': 0.7035175879396985,
  'support': 394},
 '3': {'precision': 0.6162528216704289,
  'recall': 0.6964285714285714,
  'f1-score': 0.6538922155688622,
  'support': 392},
 '4': {'precision': 0.7377892030848329,
  'recall': 0.7454545454545455,
  'f1-score': 0.7416020671834624,
  'support': 385},
 '5': {'precision': 0.7955974842767296,
  'recall': 0.640506329113924,
  'f1-score': 0.7096774193548387,
  'support': 395},
 '6': {'precision': 0.7908653846153846,
  'recall': 0.8435897435897436,
  'f1-score': 0.8163771712158808,
  'support': 390},
 '7': {'precision': 0.84375,
  'recall': 0.75,
  'f1-score': 0.7941176470588235,
  'support': 396},
 '8': {'precision': 0.8837

In [ ]:
results_2 = {
        'Vectorizer': 'TfidfVectorizer',
        'Hyperparameters': grid_search_2.best_params_,
        'Algorithm': 'GradientBoostingClassifier',
        'Cross-validation score': grid_search_2.best_score_,
        'Test score': accuracy_score_2,
        'Classification report': report_2

    }

Логістична регресія виявилась більш ефективним та швидшим (за часовими затратами) методом.
Логістична регресія менш схильна до перенавчання на невеликих наборах даних (в аналізованому - близько 20 000 дописів (11314 в трейні і приблизно 7700 в тесті)).
Також гірша результативність бустингу може бути повʼязана із розрідженістю даних та великою кількістю фіч.
бустинг не найкращий варіант для роботи з високорозмірними даними як тексти, зображення й звук.


In [ ]:
from sklearn.pipeline import FeatureUnion

In [ ]:
pipeline_3= Pipeline([
    ('features', FeatureUnion([
        ('word', TfidfVectorizer(analyzer='word', ngram_range=(1,2), max_features = 30000, max_df = 0.2, min_df = 1)),
        ('char', TfidfVectorizer(analyzer='char', ngram_range=(3,7), max_features = 30000,max_df = 0.2, min_df = 1))
    ])),
    ('clf', LogisticRegression(C=10, max_iter = 1000))
])


In [ ]:
pipeline_3.fit(train['data'], train['target'])

Pipeline(steps=[('features',
                 FeatureUnion(transformer_list=[('word',
                                                 TfidfVectorizer(max_df=0.2,
                                                                 max_features=30000,
                                                                 ngram_range=(1,
                                                                              2))),
                                                ('char',
                                                 TfidfVectorizer(analyzer='char',
                                                                 max_df=0.2,
                                                                 max_features=30000,
                                                                 ngram_range=(3,
                                                                              7)))])),
                ('clf', LogisticRegression(C=10, max_iter=1000))])

In [ ]:
predictions_3 = pipeline_3.predict(test["data"])
accuracy_score(test["target"], predictions_3)

0.8266064790228359

In [ ]:
eli5.show_prediction(pipeline_3[1], test["data"][1500], top=100, vec=pipeline_3[0],
feature_names=pipeline_3[0].get_feature_names_out(), target_names=test.target_names)

In [ ]:
pipeline_3.fit(cleaned_train['data'], cleaned_train['target'])

Pipeline(steps=[('features',
                 FeatureUnion(transformer_list=[('word',
                                                 TfidfVectorizer(max_df=0.2,
                                                                 max_features=30000,
                                                                 ngram_range=(1,
                                                                              2))),
                                                ('char',
                                                 TfidfVectorizer(analyzer='char',
                                                                 max_df=0.2,
                                                                 max_features=30000,
                                                                 ngram_range=(3,
                                                                              7)))])),
                ('clf', LogisticRegression(C=10, max_iter=1000))])

In [ ]:
predictions_4 = pipeline_3.predict(cleaned_test
["data"])
accuracy_score(cleaned_test["target"], predictions_4)

0.8311205523101434

In [ ]:
eli5.explain_weights(pipeline_3[1], feature_names=pipeline_3[0].get_feature_names_out(), target_names=test.target_names)

Explanation(estimator='LogisticRegression(C=10, max_iter=1000)', description="\nFeatures with largest coefficients per class.\nCaveats:\n1. Be careful with features which are not\n   independent - weights don't show their importance.\n2. If scale of input features is different then scale of coefficients\n   will also be different, making direct comparison between coefficient values\n   incorrect.\n3. Depending on regularization, rare features sometimes may have high\n   coefficients; this doesn't mean they contribute much to the\n   classification result for most examples.\n", error=None, method='linear model', is_regression=False, targets=[TargetExplanation(target='alt.atheism', feature_weights=FeatureWeights(pos=[FeatureWeight(feature='word__keith', weight=2.5649968131055707, std=None, value=None), FeatureWeight(feature='word__atheism', weight=2.5462816539533324, std=None, value=None), FeatureWeight(feature='char__theis', weight=2.2160273202663636, std=None, value=None), FeatureWeight(feature='char__heis', weight=2.208662082814845, std=None, value=None), FeatureWeight(feature='word__enviroleague', weight=2.150948054099153, std=None, value=None), FeatureWeight(feature='word__god', weight=2.117131560677153, std=None, value=None), FeatureWeight(feature='word__rushdie', weight=2.075825122942901, std=None, value=None), FeatureWeight(feature='word__islamic', weight=2.07189950493229, std=None, value=None), FeatureWeight(feature='word__mathew', weight=2.031070819265848, std=None, value=None), FeatureWeight(feature='word__wingate', weight=2.001156692803197, std=None, value=None), FeatureWeight(feature='word__okcforum', weight=1.9364104679692902, std=None, value=None), FeatureWeight(feature='word__jaeger', weight=1.9072704301729833, std=None, value=None), FeatureWeight(feature='word__cobb', weight=1.8883822158906634, std=None, value=None), FeatureWeight(feature='char__athei', weight=1.8666755186183819, std=None, value=None), FeatureWeight(feature='char__ athei', weight=1.8642084931015361, std=None, value=None), FeatureWeight(feature='char__atheis', weight=1.836260636799172, std=None, value=None), FeatureWeight(feature='char__ atheis', weight=1.8337918460884213, std=None, value=None), FeatureWeight(feature='word__bible', weight=1.8002711071535633, std=None, value=None), FeatureWeight(feature='word__mangoe', weight=1.7393079648719902, std=None, value=None), FeatureWeight(feature='char__eis', weight=1.7080296881543657, std=None, value=None)], neg=[], pos_remaining=22849, neg_remaining=37132), proba=None, score=None, weighted_spans=None, heatmap=None), TargetExplanation(target='comp.graphics', feature_weights=FeatureWeights(pos=[FeatureWeight(feature='word__3d', weight=3.7780486994404074, std=None, value=None), FeatureWeight(feature='word__graphics', weight=3.4511310118306704, std=None, value=None), FeatureWeight(feature='word__pov', weight=3.317047942635948, std=None, value=None), FeatureWeight(feature='word__tiff', weight=3.1993068238971474, std=None, value=None), FeatureWeight(feature='word__3do', weight=3.1417096403907503, std=None, value=None), FeatureWeight(feature='char__ 3d', weight=3.058575319794801, std=None, value=None), FeatureWeight(feature='word__cview', weight=3.030012186811914, std=None, value=None), FeatureWeight(feature='word__image', weight=2.8473046908094473, std=None, value=None), FeatureWeight(feature='word__polygon', weight=2.777889910748308, std=None, value=None), FeatureWeight(feature='word__mpeg', weight=2.6813753385376837, std=None, value=None), FeatureWeight(feature='word__vesa', weight=2.6497087951541194, std=None, value=None), FeatureWeight(feature='char__ imag', weight=2.5000596330201654, std=None, value=None), FeatureWeight(feature='char__ima', weight=2.397860943550521, std=None, value=None), FeatureWeight(feature='word__animation', weight=2.387824012544957, std=None, value=None), FeatureWeight(feature='char__ ima', weight=2.3266967001814916, std=None, value=None), FeatureWeight(feature='char__imag', weight

In [ ]:
eli5.show_prediction(pipeline_3[1], cleaned_test["data"][1500], top = 100, vec=pipeline_3[0],
feature_names=pipeline_3[0].get_feature_names_out(), target_names=cleaned_test.target_names)

In [ ]:
pipeline_4 = Pipeline([
    ('features', FeatureUnion([
        ('word', TfidfVectorizer(analyzer='word', ngram_range=(1,2), max_features = 40000, max_df = 0.95, min_df = 1)),
        ('char', TfidfVectorizer(analyzer='char', ngram_range=(3,7), max_features = 40000,max_df = 0.95, min_df = 1))
    ])),
    ('clf', LogisticRegression(C=10, max_iter = 1000))
])


In [ ]:
pipeline_4.fit(train['data'], train['target'])

Pipeline(steps=[('features',
                 FeatureUnion(transformer_list=[('word',
                                                 TfidfVectorizer(max_df=0.95,
                                                                 max_features=40000,
                                                                 ngram_range=(1,
                                                                              2))),
                                                ('char',
                                                 TfidfVectorizer(analyzer='char',
                                                                 max_df=0.95,
                                                                 max_features=40000,
                                                                 ngram_range=(3,
                                                                              7)))])),
                ('clf', LogisticRegression(C=10, max_iter=1000))])

In [ ]:
# max_features = 40000, max_df = 0.95, min_df = 1
predictions_9 = pipeline_4.predict(test["data"])
accuracy_score(test["target"], predictions_9)

0.8276686139139671

In [ ]:
eli5.show_prediction(pipeline_4[1], test["data"][1500], top = 100, vec=pipeline_4[0],
feature_names=pipeline_4[0].get_feature_names_out(), target_names=test.target_names)

In [ ]:
eli5.show_prediction(pipeline_4[1], test["data"][1500], top = 100, vec=pipeline_4[0],
feature_names=pipeline_4[0].get_feature_names_out(), target_names=test.target_names)

In [ ]:
# max_features = 40000, max_df = 0.85, min_df = 1
predictions_8 = pipeline_4.predict(test["data"])
accuracy_score(test["target"], predictions_8)

0.8287307488050982

In [ ]:
eli5.explain_weights(pipeline_4[1], feature_names=pipeline_4[0].get_feature_names_out(), target_names=test.target_names)

Explanation(estimator='LogisticRegression(C=10, max_iter=1000)', description="\nFeatures with largest coefficients per class.\nCaveats:\n1. Be careful with features which are not\n   independent - weights don't show their importance.\n2. If scale of input features is different then scale of coefficients\n   will also be different, making direct comparison between coefficient values\n   incorrect.\n3. Depending on regularization, rare features sometimes may have high\n   coefficients; this doesn't mean they contribute much to the\n   classification result for most examples.\n", error=None, method='linear model', is_regression=False, targets=[TargetExplanation(target='alt.atheism', feature_weights=FeatureWeights(pos=[FeatureWeight(feature='word__atheism', weight=3.2623878379108735, std=None, value=None), FeatureWeight(feature='word__keith', weight=3.2094639307447563, std=None, value=None), FeatureWeight(feature='word__enviroleague', weight=3.043826042641088, std=None, value=None), FeatureWeight(feature='word__god', weight=2.7624558069111207, std=None, value=None), FeatureWeight(feature='word__atheists', weight=2.5530789053882232, std=None, value=None), FeatureWeight(feature='word__islamic', weight=2.3987686016242193, std=None, value=None), FeatureWeight(feature='word__cobb', weight=2.3946777567188526, std=None, value=None), FeatureWeight(feature='word__mathew', weight=2.268069302909515, std=None, value=None), FeatureWeight(feature='word__rushdie', weight=2.1417195809422096, std=None, value=None), FeatureWeight(feature='word__bible', weight=2.11328977575142, std=None, value=None), FeatureWeight(feature='word__is', weight=2.093972070710896, std=None, value=None), FeatureWeight(feature='char__theis', weight=2.039923638132891, std=None, value=None), FeatureWeight(feature='char__heis', weight=2.031959965626081, std=None, value=None), FeatureWeight(feature='word__edu keith', weight=1.9872724922092921, std=None, value=None), FeatureWeight(feature='word__okcforum', weight=1.9643134602541412, std=None, value=None), FeatureWeight(feature='word__wingate', weight=1.9256867671307474, std=None, value=None), FeatureWeight(feature='word__jaeger', weight=1.8683333822810224, std=None, value=None), FeatureWeight(feature='char__athei', weight=1.7718155886510796, std=None, value=None), FeatureWeight(feature='char__atheis', weight=1.7490690272792226, std=None, value=None), FeatureWeight(feature='word__wesleyan', weight=1.7384060263837935, std=None, value=None)], neg=[], pos_remaining=28004, neg_remaining=51977), proba=None, score=None, weighted_spans=None, heatmap=None), TargetExplanation(target='comp.graphics', feature_weights=FeatureWeights(pos=[FeatureWeight(feature='word__graphics', weight=5.950322530244027, std=None, value=None), FeatureWeight(feature='word__3d', weight=4.748981324218858, std=None, value=None), FeatureWeight(feature='word__pov', weight=4.088597237960528, std=None, value=None), FeatureWeight(feature='word__image', weight=3.91445068906165, std=None, value=None), FeatureWeight(feature='word__tiff', weight=3.569414808988912, std=None, value=None), FeatureWeight(feature='word__3do', weight=3.5134174728221104, std=None, value=None), FeatureWeight(feature='word__cview', weight=3.3316405366859616, std=None, value=None), FeatureWeight(feature='word__animation', weight=3.269515200635224, std=None, value=None), FeatureWeight(feature='word__polygon', weight=3.217742629063571, std=None, value=None), FeatureWeight(feature='word__images', weight=3.060475620964915, std=None, value=None), FeatureWeight(feature='word__vga', weight=2.71653700334056, std=None, value=None), FeatureWeight(feature='word__files', weight=2.7072323776522733, std=None, value=None), FeatureWeight(feature='word__points', weight=2.6312505311831575, std=None, value=None), FeatureWeight(feature='word__vesa', weight=2.6233369277557474, std=None, value=None), FeatureWeight(feature='word__gif', weight=2.617022478538799, std=None, value=None), FeatureWeight(feature='word_____', we

In [ ]:
#max_df = 0.25 і 0.25, max_features = 40000, 30000
predictions_7 = pipeline_4.predict(test["data"])
accuracy_score(test["target"], predictions_7)

0.8276686139139671

In [ ]:
eli5.show_prediction(pipeline_4[1], test["data"][1500], top = 100, vec=pipeline_4[0],
feature_names=pipeline_4[0].get_feature_names_out(), target_names=test.target_names)

In [ ]:
# max_features = 40000, max_df = 0.85, min_df = 2, max_features = 30000,max_df = 0.85, min_df = 2))
predictions_6 = pipeline_4.predict(test["data"])
accuracy_score(test["target"], predictions_6)

0.8252788104089219

In [ ]:
eli5.show_prediction(pipeline_4[1], test["data"][1500], top = 100, vec=pipeline_4[0],
feature_names=pipeline_4[0].get_feature_names_out(), target_names=test.target_names)

In [ ]:
#max_df = 0.8
predictions_5 = pipeline_4.predict(test["data"])
accuracy_score(test["target"], predictions_5)

0.8243494423791822

In [ ]:
# max_features = 15000, max_df = 0.6, min_df = 2, max_features = 20000,max_df = 0.65, min_df = 2))
predictions_5 = pipeline_4.predict(test["data"])
accuracy_score(test["target"], predictions_5)

0.8113382899628253

In [ ]:
# max_features = 30000, max_df = 0.6, min_df = 2, max_features = 30000,max_df = 0.65, min_df = 2))
predictions_5 = pipeline_4.predict(test["data"])
accuracy_score(test["target"], predictions_5)

0.8244822092405736

In [ ]:
eli5.show_prediction(pipeline_4[1], test["data"][1500], top = 100, vec=pipeline_4[0],
feature_names=pipeline_4[0].get_feature_names_out(), target_names=test.target_names)